# Recommend the place to live in east Phoenix Area by analyzing house price and venues data

### A. Introduction

#### A.1. Description of Back Ground and Problem
<br>A.1.1. The United States economy is on the brink of hitting its longest-lasting period of growth ever — but no one can quite get the idea of a coming recession out of their heads. Several signals such as inverted yield curve and lead economic index has turn red, which making most people afraid that depression will not be too far.
During the recession, many economic elements, which intimately related to people's lives, such as gas price, traffic, salary, employment, have been greatly affected. The house price belongs to one of these economic elements. During last recession, the house price reached the peak and sharply dropped after the recession began.
<br>A.1.2. I love the place I live in the Columbus, Ohio. But I will move to Arizona, east Phoenix Area. I plan to own a house, whether by renting or purchasing, and I hope that the community environment of the house, in which I will live, are pretty the same as I’m living right now. I hope the price of the house I will buy or long rent won’t drop significant during recession.


#### A.2. Data Description
<br>   To consider the problem we can list the data as below:
<br>   1. House price data: will use the Five-Digit ZIP Codes Annual House Price Indexes (Developmental Index; Not Seasonally Adjusted) to represent the house price.
<br>   2. US zipcode with some basic data
<br>   3. Venues data :  will use Forsquare API to get the most common venues of given Zip code of Phoenix Area and Columbus.


In [1]:
import numpy as np
import pandas as pd 
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
import json 
from geopy.geocoders import Nominatim 
import requests 
from pandas.io.json import json_normalize 
import matplotlib.cm as cm
import matplotlib.colors as colors
from sklearn.cluster import KMeans
from sklearn.datasets.samples_generator import make_blobs
from bs4 import BeautifulSoup 
import lxml
import math

<br>

### B.Preprocessing the data

#### B.1.Read the data of Zip code and House price and the data of Arizona Zip code

In [2]:
H_z = pd.read_csv('C:/Users/lingl/Desktop/New folder/Zip_with_House_price.csv')
L_d = pd.read_csv('C:/Users/lingl/Desktop/New folder/uszips.csv')

In [45]:
import pandas_profiling

In [52]:
profile= pandas_profiling.ProfileReport(H_z)

In [53]:
profile

In [54]:
profile2 = pandas_profiling.ProfileReport(L_d)
profile2

In [3]:
Zip_live_now = 43201

In [4]:
H_z.tail()

Five-Digit ZIP Code  Year Annual Change (%)     HPI  \
539199                99901  2014              4.03  233.62   
539200                99901  2015              5.37  246.16   
539201                99901  2016              0.83  248.21   
539202                99901  2017             -0.16  247.80   
539203                99901  2018              6.73  264.48   

       HPI with 1990 base HPI with 2000 base  Unnamed: 6  Unnamed: 7  
539199             218.61             157.64         NaN         NaN  
539200             230.34             166.10         NaN         NaN  
539201             232.26             167.49         NaN         NaN  
539202             231.88             167.21         NaN         NaN  
539203             247.48             178.47         NaN         NaN

In [5]:
L_d.head()

zip       lat       lng       city state_id   state_name  zcta  \
0  601  18.18004 -66.75218   Adjuntas       PR  Puerto Rico  True   
1  602  18.36073 -67.17517     Aguada       PR  Puerto Rico  True   
2  603  18.45439 -67.12202  Aguadilla       PR  Puerto Rico  True   
3  606  18.16724 -66.93828    Maricao       PR  Puerto Rico  True   
4  610  18.29032 -67.12243     Anasco       PR  Puerto Rico  True   

   parent_zcta  population  density  county_fips county_name  \
0          NaN       18570    111.4        72001    Adjuntas   
1          NaN       41520    523.5        72003      Aguada   
2          NaN       54689    667.9        72005   Aguadilla   
3          NaN        6615     60.4        72093     Maricao   
4          NaN       29016    312.0        72011      Añasco   

                          all_county_weights  imprecise  military  \
0               {'72001':99.43,'72141':0.57}      False     False   
1                              {'72003':100}      False     False   
2                              {'72005':100}      False     False   
3  {'72093':94.88,'72121':1.35,'72153':3.78}      False     False   
4               {'72003':0.55,'72011':99.45}      False     False   

              timezone  
0  America/Puerto_Rico  
1  America/Puerto_Rico  
2  America/Puerto_Rico  
3  America/Puerto_Rico  
4  America/Puerto_Rico

Get the data that only contain the zipcode that I care

In [6]:
L_d = L_d[L_d['state_id'].isin(['AZ','OH'])]
H_z = H_z[H_z['Five-Digit ZIP Code'].isin(L_d['zip'].unique().tolist())]

This is the geo distance function with 1.2 to meet with the real distance

In [7]:
def Circle_Distance(x1, y1, x2, y2):
    # Greate circle distance between points.
    x1=x1/180*math.pi
    y1=y1/180*math.pi
    x2=x2/180*math.pi
    y2=y2/180*math.pi
    dist = 1.2*3959*2*math.asin(math.sqrt(math.sin(abs(x1-x2)/2)**2+math.cos(x1)*math.cos(x2)*math.sin(abs(y1-y2)/2)**2))
    return dist

<br>

#### B.2.Calculate the neighborhood by using distance between each zipcode, the distance will determind by geo distance*1.2 
The distance to verify is neighborhood less or equal to 6km

In [8]:
def get_neighborhood(data,state,_zip,threshod):
    neigh=[]
    for __zip in data[data['state_id']==state]['zip'].unique().tolist():
        dist = Circle_Distance(data[data['zip']==_zip]['lat'].values[0],data[data['zip']==_zip]['lng'].values[0],data[data['zip']==__zip]['lat'].values[0],data[data['zip']==__zip]['lng'].values[0])
        if dist<= threshod:
            neigh.append([__zip,data[data['zip']==__zip]['lat'].values[0],data[data['zip']==__zip]['lng'].values[0]])
    return neigh
dic = {}
cont=[]
for zip_ in L_d[L_d['city'].isin(['Apache Junction','Chandler','Gilbert','Guadalupe','Mesa','Tempe','Queen Creek'])]['zip'].unique().tolist():
    try:
        dic[zip_] = get_neighborhood(L_d,'AZ',zip_,6)
    except:
        cont.append(zip_)


In [9]:
dic[43201] = get_neighborhood(L_d,'OH',43201,6)

<br>

#### B.3. Get Foursuqard data and give the neigborhood catergory

In [10]:
CLIENT_ID = 'JBREGZ4UNA53HX43WMAD4TQ2X2XJWMX5DPHEZEIZHQA0ACNP' # your Foursquare ID
CLIENT_SECRET = 'VNS40KF3V4MGSWWAV0IGQINZIGIT1EQKNCWBFPOS3QF1JMOJ' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: JBREGZ4UNA53HX43WMAD4TQ2X2XJWMX5DPHEZEIZHQA0ACNP
CLIENT_SECRET:VNS40KF3V4MGSWWAV0IGQINZIGIT1EQKNCWBFPOS3QF1JMOJ


In [11]:
CLIENT_ID2 = 'WYT3JAZM2TK1TBTPC3AJKGWL5Z2JMXSASQN4KOJQI1HXJB10'
CLIENT_SECRET2 = '5B5KZV1IU5JLSRGTYQN5QWKUJITRXXIA33CVD2VTI5C1HSOU'

Utilized the Foursquare API to explore the boroughs and segment the neighbor. To get the almost all the insight of the neighbor, I set the limit as 500 venues. And also to cover the place that I can reach by car I set the radius 5000 meter for each neighbor from their given latitude and longitude informations. 
<br>This will return all the category of each neighbor for the place I care about

In [13]:
venues_list=[]
no = []
for _zip, value in dic.items():
    for i in range(len(value)):
        name = _zip; neighbor = value[i][0]; lat = value[i][1]; lng = value[i][2]
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
                CLIENT_ID2, 
                CLIENT_SECRET2, 
                VERSION, 
                lat,
                lng,
                5000, 
                500)
        try:
            results = requests.get(url).json()["response"]['groups'][0]['items']
            for v in results:
                cate = v['venue']['categories'][0]['name']
                lat_ = v['venue']['location']['lat']
                lng_ = v['venue']['location']['lng']
                dist_ = Circle_Distance(L_d[L_d['zip']==_zip]['lat'], L_d[L_d['zip']==_zip]['lng'], lat_, lng_)
                venues_list.append([_zip,cate,dist_])
        except:
            print(_zip,neighbor)
            no.append([np,_zip])

In [14]:
venues_list

[[85119, 'Trail', 2.591600140371613],
 [85119, 'Concert Hall', 1.6793499477629288],
 [85119, 'Bar', 3.5757443486821816],
 [85119, 'Pharmacy', 3.3216833709864537],
 [85119, 'Pharmacy', 3.1307714091037235],
 [85119, 'Golf Course', 3.6026641004167974],
 [85119, 'Country Dance Club', 2.436842121597838],
 [85119, 'Mexican Restaurant', 3.4099965939307646],
 [85119, 'Museum', 3.085720203322666],
 [85119, 'Convenience Store', 3.0283224028780413],
 [85119, 'Farmers Market', 3.419155424947623],
 [85119, 'Grocery Store', 2.9554405495563665],
 [85119, 'Breakfast Spot', 3.465855900028574],
 [85119, 'Fast Food Restaurant', 3.159138855558464],
 [85119, 'American Restaurant', 3.526373106823307],
 [85119, 'American Restaurant', 3.4397359705873694],
 [85119, 'Discount Store', 3.5885583656118105],
 [85119, 'Coffee Shop', 3.2775131407937956],
 [85119, 'Video Store', 2.5591592652542583],
 [85119, 'Clothing Store', 3.197672669985038],
 [85119, 'American Restaurant', 2.552901993647399],
 [85119, 'Pizza Place

#### B.4.The following will make a matrix to evalate the similarity of both the place I live now and the place I may will live in the future 

In [15]:
category_data = pd.DataFrame(venues_list,columns=['zip','cate','distance'])

In [16]:
category_data.head()

zip          cate  distance
0  85119         Trail  2.591600
1  85119  Concert Hall  1.679350
2  85119           Bar  3.575744
3  85119      Pharmacy  3.321683
4  85119      Pharmacy  3.130771

In [17]:
cate_list = sorted(category_data['cate'].unique().tolist())

In [18]:
cate = pd.DataFrame(pd.merge(pd.pivot_table(category_data,values=['cate'],columns=['cate'],index=['zip'],aggfunc=(lambda x:len(x.dropna().unique()))).fillna(0),
                pd.pivot_table(category_data,values=['distance'],columns=['cate'],index=['zip'],aggfunc=np.mean).fillna(-1),
                on=['zip']).reset_index().values,columns=['zip']+cate_list+['dist_'+x for x in cate_list])

In [19]:
cate.head()

zip  ATM  Accessories Store  Adult Boutique  Advertising Agency  \
0  43201.0  0.0                0.0             0.0                 0.0   
1  85119.0  0.0                0.0             0.0                 0.0   
2  85120.0  0.0                0.0             0.0                 0.0   
3  85142.0  0.0                0.0             0.0                 0.0   
4  85201.0  0.0                0.0             0.0                 1.0   

   Airport  Airport Lounge  Airport Service  Airport Terminal  \
0      0.0             0.0              2.0               0.0   
1      0.0             0.0              0.0               0.0   
2      0.0             0.0              0.0               0.0   
3      1.0             0.0              0.0               0.0   
4      1.0             0.0              0.0               0.0   

   Alternative Healer  American Restaurant  Animal Shelter  Antique Shop  \
0                 0.0                 31.0             1.0           2.0   
1                 0.0                  3.0             0.0           1.0   
2                 0.0                  6.0             0.0           3.0   
3                 0.0                  0.0             0.0           0.0   
4                 0.0                 13.0             0.0           1.0   

   Arcade  Arepa Restaurant  Art Gallery  Art Museum  Arts & Crafts Store  \
0     1.0               1.0          3.0         1.0                  2.0   
1     0.0               0.0          0.0         0.0                  0.0   
2     0.0               0.0          0.0         0.0                  0.0   
3     0.0               0.0          0.0         0.0                  0.0   
4     3.0               1.0          0.0         2.0                  2.0   

   Asian Restaurant  Athletics & Sports  Auto Dealership  Auto Garage  \
0               6.0                 4.0              0.0          0.0   
1               0.0                 0.0              0.0          0.0   
2               2.0                 0.0              0.0          0.0   
3               0.0                 0.0              0.0          0.0   
4               7.0                 1.0              1.0          0.0   

   Automotive Shop  BBQ Joint  Bagel Shop  Bakery  Bank   Bar  Baseball Field  \
0              0.0        6.0         1.0    18.0   7.0  33.0             1.0   
1              0.0        0.0         0.0     2.0   2.0   1.0             0.0   
2              0.0        0.0         1.0     2.0   4.0   2.0             1.0   
3              0.0        0.0         0.0     0.0   0.0   0.0             0.0   
4              0.0        5.0         1.0     7.0   1.0  10.0             5.0   

   Baseball Stadium  Basketball Court  Bavarian Restaurant  Bed & Breakfast  \
0               1.0               1.0                  1.0              0.0   
1               0.0               0.0                  0.0              0.0   
2               0.0               0.0                  0.0              0.0   
3               0.0               0.0                  0.0              0.0   
4               3.0               2.0                  0.0              0.0   

   Beer Bar  Beer Garden  Beer Store  Big Box Store  Bike Shop  Bistro  \
0       3.0          2.0         2.0            1.0        0.0     2.0   
1       0.0          0.0         0.0            0.0        1.0     0.0   
2       0.0          0.0         0.0            0.0        1.0     0.0   
3       0.0          0.0         0.0            0.0        0.0     1.0   
4       0.0          1.0         1.0            2.0        1.0     1.0   

   Bookstore  Botanical Garden  Boutique  Bowling Alley  Brazilian Restaurant  \
0        3.0               0.0       1.0            2.0                   1.0   
1        0.0               0.0       0.0            0.0                   0.0   
2        0.0               0.0       0.0            0.0                   0.0   
3        0.0               0.0       0.0            0.0                   0.0   


In [20]:
Zipdata = pd.merge(cate,L_d,on='zip')

In [21]:
Zipdata.drop(['lat','lng','state_id','city','state_name','zcta','parent_zcta','county_fips','county_name','all_county_weights','imprecise','military','timezone'],axis=1,inplace=True)

In [22]:
Zipdata.head()

zip  ATM  Accessories Store  Adult Boutique  Advertising Agency  \
0  43201.0  0.0                0.0             0.0                 0.0   
1  85119.0  0.0                0.0             0.0                 0.0   
2  85120.0  0.0                0.0             0.0                 0.0   
3  85142.0  0.0                0.0             0.0                 0.0   
4  85201.0  0.0                0.0             0.0                 1.0   

   Airport  Airport Lounge  Airport Service  Airport Terminal  \
0      0.0             0.0              2.0               0.0   
1      0.0             0.0              0.0               0.0   
2      0.0             0.0              0.0               0.0   
3      1.0             0.0              0.0               0.0   
4      1.0             0.0              0.0               0.0   

   Alternative Healer  American Restaurant  Animal Shelter  Antique Shop  \
0                 0.0                 31.0             1.0           2.0   
1                 0.0                  3.0             0.0           1.0   
2                 0.0                  6.0             0.0           3.0   
3                 0.0                  0.0             0.0           0.0   
4                 0.0                 13.0             0.0           1.0   

   Arcade  Arepa Restaurant  Art Gallery  Art Museum  Arts & Crafts Store  \
0     1.0               1.0          3.0         1.0                  2.0   
1     0.0               0.0          0.0         0.0                  0.0   
2     0.0               0.0          0.0         0.0                  0.0   
3     0.0               0.0          0.0         0.0                  0.0   
4     3.0               1.0          0.0         2.0                  2.0   

   Asian Restaurant  Athletics & Sports  Auto Dealership  Auto Garage  \
0               6.0                 4.0              0.0          0.0   
1               0.0                 0.0              0.0          0.0   
2               2.0                 0.0              0.0          0.0   
3               0.0                 0.0              0.0          0.0   
4               7.0                 1.0              1.0          0.0   

   Automotive Shop  BBQ Joint  Bagel Shop  Bakery  Bank   Bar  Baseball Field  \
0              0.0        6.0         1.0    18.0   7.0  33.0             1.0   
1              0.0        0.0         0.0     2.0   2.0   1.0             0.0   
2              0.0        0.0         1.0     2.0   4.0   2.0             1.0   
3              0.0        0.0         0.0     0.0   0.0   0.0             0.0   
4              0.0        5.0         1.0     7.0   1.0  10.0             5.0   

   Baseball Stadium  Basketball Court  Bavarian Restaurant  Bed & Breakfast  \
0               1.0               1.0                  1.0              0.0   
1               0.0               0.0                  0.0              0.0   
2               0.0               0.0                  0.0              0.0   
3               0.0               0.0                  0.0              0.0   
4               3.0               2.0                  0.0              0.0   

   Beer Bar  Beer Garden  Beer Store  Big Box Store  Bike Shop  Bistro  \
0       3.0          2.0         2.0            1.0        0.0     2.0   
1       0.0          0.0         0.0            0.0        1.0     0.0   
2       0.0          0.0         0.0            0.0        1.0     0.0   
3       0.0          0.0         0.0            0.0        0.0     1.0   
4       0.0          1.0         1.0            2.0        1.0     1.0   

   Bookstore  Botanical Garden  Boutique  Bowling Alley  Brazilian Restaurant  \
0        3.0               0.0       1.0            2.0                   1.0   
1        0.0               0.0       0.0            0.0                   0.0   
2        0.0               0.0       0.0            0.0                   0.0   
3        0.0               0.0       0.0            0.0                   0.0   


### C.Define the similarity between target and choice

#### C.1. Similarity model and scale data
To calculate the distance, I decide to use combin cosine similarity

In [23]:
from sklearn.metrics.pairwise import cosine_similarity
from sklearn.preprocessing import MinMaxScaler

In [24]:
zip_list = Zipdata['zip'].unique().tolist()
Zipdata_ = Zipdata.copy()
scale = MinMaxScaler(feature_range=(0, 1)).fit(Zipdata_.iloc[:,1:]) 

In [25]:
Zipdata_.iloc[:,1:]=scale.transform(Zipdata_.iloc[:,1:])

In [26]:
Zipdata_.head()

zip  ATM  Accessories Store  Adult Boutique  Advertising Agency  \
0  43201.0  0.0                0.0             0.0                 0.0   
1  85119.0  0.0                0.0             0.0                 0.0   
2  85120.0  0.0                0.0             0.0                 0.0   
3  85142.0  0.0                0.0             0.0                 0.0   
4  85201.0  0.0                0.0             0.0                 1.0   

   Airport  Airport Lounge  Airport Service  Airport Terminal  \
0      0.0             0.0              1.0               0.0   
1      0.0             0.0              0.0               0.0   
2      0.0             0.0              0.0               0.0   
3      0.5             0.0              0.0               0.0   
4      0.5             0.0              0.0               0.0   

   Alternative Healer  American Restaurant  Animal Shelter  Antique Shop  \
0                 0.0             1.000000             1.0      0.666667   
1                 0.0             0.096774             0.0      0.333333   
2                 0.0             0.193548             0.0      1.000000   
3                 0.0             0.000000             0.0      0.000000   
4                 0.0             0.419355             0.0      0.333333   

     Arcade  Arepa Restaurant  Art Gallery  Art Museum  Arts & Crafts Store  \
0  0.333333               1.0          1.0         0.5             0.666667   
1  0.000000               0.0          0.0         0.0             0.000000   
2  0.000000               0.0          0.0         0.0             0.000000   
3  0.000000               0.0          0.0         0.0             0.000000   
4  1.000000               1.0          0.0         1.0             0.666667   

   Asian Restaurant  Athletics & Sports  Auto Dealership  Auto Garage  \
0          0.666667                1.00              0.0          0.0   
1          0.000000                0.00              0.0          0.0   
2          0.222222                0.00              0.0          0.0   
3          0.000000                0.00              0.0          0.0   
4          0.777778                0.25              1.0          0.0   

   Automotive Shop  BBQ Joint  Bagel Shop    Bakery      Bank       Bar  \
0              0.0   0.857143    0.333333  1.000000  0.538462  1.000000   
1              0.0   0.000000    0.000000  0.111111  0.153846  0.030303   
2              0.0   0.000000    0.333333  0.111111  0.307692  0.060606   
3              0.0   0.000000    0.000000  0.000000  0.000000  0.000000   
4              0.0   0.714286    0.333333  0.388889  0.076923  0.303030   

   Baseball Field  Baseball Stadium  Basketball Court  Bavarian Restaurant  \
0             0.2          0.333333               0.5                  1.0   
1             0.0          0.000000               0.0                  0.0   
2             0.2          0.000000               0.0                  0.0   
3             0.0          0.000000               0.0                  0.0   
4             1.0          1.000000               1.0                  0.0   

   Bed & Breakfast  Beer Bar  Beer Garden  Beer Store  Big Box Store  \
0              0.0       1.0          1.0         1.0            0.5   
1              0.0       0.0          0.0         0.0            0.0   
2              0.0       0.0          0.0         0.0            0.0   
3              0.0       0.0          0.0         0.0            0.0   
4              0.0       0.0          0.5         0.5            1.0   

   Bike Shop  Bistro  Bookstore  Botanical Garden  Boutique  Bowling Alley  \
0        0.0     1.0        0.6               0.0       0.5            1.0   
1        1.0     0.0        0.0               0.0       0.0            0.0   
2        1.0     0.0        0.0               0.0       0.0            0.0   
3        0.0     0.5        0.0               0.0       0.0            0.0   
4        1.0     0.5        0.6               1.0       0

#### C.2.More care about how much the choice can implace the target 

So I choose to only keep the categories that target has

In [27]:
for cate in cate_list:
    if Zipdata[Zipdata['zip']==43201][cate].values[0]==0:
        Zipdata_.drop([cate,'dist_'+cate],axis=1,inplace=True)
y = Zipdata_[Zipdata_['zip']==43201].iloc[:,1:].values
result_list=[]
for zip_ in [x for x in zip_list if x != 43201]:
    x =Zipdata_[Zipdata_['zip']==zip_].iloc[:,1:].values
    sim = cosine_similarity(x,y)[0][0]
    result_list.append([zip_,sim])

In [58]:
pandas_profiling.ProfileReport(Zipdata_)

In [59]:
Zipdata_.head()

zip  Airport Service  American Restaurant  Animal Shelter  \
0  43201.0              1.0             1.000000             1.0   
1  85119.0              0.0             0.096774             0.0   
2  85120.0              0.0             0.193548             0.0   
3  85142.0              0.0             0.000000             0.0   
4  85201.0              0.0             0.419355             0.0   

   Antique Shop    Arcade  Arepa Restaurant  Art Gallery  Art Museum  \
0      0.666667  0.333333               1.0          1.0         0.5   
1      0.333333  0.000000               0.0          0.0         0.0   
2      1.000000  0.000000               0.0          0.0         0.0   
3      0.000000  0.000000               0.0          0.0         0.0   
4      0.333333  1.000000               1.0          0.0         1.0   

   Arts & Crafts Store  Asian Restaurant  Athletics & Sports  BBQ Joint  \
0             0.666667          0.666667                1.00   0.857143   
1             0.000000          0.000000                0.00   0.000000   
2             0.000000          0.222222                0.00   0.000000   
3             0.000000          0.000000                0.00   0.000000   
4             0.666667          0.777778                0.25   0.714286   

   Bagel Shop    Bakery      Bank       Bar  Baseball Field  Baseball Stadium  \
0    0.333333  1.000000  0.538462  1.000000             0.2          0.333333   
1    0.000000  0.111111  0.153846  0.030303             0.0          0.000000   
2    0.333333  0.111111  0.307692  0.060606             0.2          0.000000   
3    0.000000  0.000000  0.000000  0.000000             0.0          0.000000   
4    0.333333  0.388889  0.076923  0.303030             1.0          1.000000   

   Basketball Court  Bavarian Restaurant  Beer Bar  Beer Garden  Beer Store  \
0               0.5                  1.0       1.0          1.0         1.0   
1               0.0                  0.0       0.0          0.0         0.0   
2               0.0                  0.0       0.0          0.0         0.0   
3               0.0                  0.0       0.0          0.0         0.0   
4               1.0                  0.0       0.0          0.5         0.5   

   Big Box Store  Bistro  Bookstore  Boutique  Bowling Alley  \
0            0.5     1.0        0.6       0.5            1.0   
1            0.0     0.0        0.0       0.0            0.0   
2            0.0     0.0        0.0       0.0            0.0   
3            0.0     0.5        0.0       0.0            0.0   
4            1.0     0.5        0.6       0.0            0.0   

   Brazilian Restaurant  Breakfast Spot   Brewery  Burger Joint  \
0                   1.0        0.666667  0.866667      0.466667   
1                   0.0        0.250000  0.000000      0.066667   
2                   0.0        0.250000  0.000000      0.200000   
3                   0.0        0.083333  0.000000      0.066667   
4                   0.0        0.833333  0.733333      0.933333   

   Business Service      Café  Cajun / Creole Restaurant  Camera Store  \
0               1.0  1.000000                       1.00           1.0   
1               0.0  0.000000                       0.00           0.0   
2               0.0  0.076923                       0.00           0.0   
3               0.0  0.000000                       0.00           0.0   
4               0.0  0.307692                       0.25           0.0   

   Candy Store  Cantonese Restaurant  Capitol Building  Caribbean Restaurant  \
0          1.0                   1.0               1.0                   1.0   
1          0.0                   0.0               0.0                   0.0   
2          0.0                   0.0               0.0                   0.0   
3          0.0                   0.0               0.0                   0.0   
4          0.0                   0.0               0.0                   1.0   

   Chinese Restaurant  Clothing Store 

In [28]:
result_s = pd.DataFrame(result_list,columns=['zip','similarity'])

In [61]:
result_s.head()

zip  similarity
0  85119.0    0.340612
1  85120.0    0.389743
2  85142.0    0.197760
3  85201.0    0.627745
4  85202.0    0.616246

### D. House Price Analysis


#### D.1. Time period determine
Then calculate the house price change within the 1 years before recession and 5 years after recession
<br>Last recession happen in 2007,2008 and 2009, so the time to be considered is 2006 to 2014

Take the price in 2006 as the initial price

In [30]:
H_z = H_z[H_z['Five-Digit ZIP Code'].isin([x for x in zip_list if x != 43201])]

In [31]:
H_dic = []
H_z=H_z[H_z['Year']>2005]
H_z['HPI'] = H_z['HPI'].apply(pd.to_numeric)
for zip_ in [x for x in zip_list if x != 43201]:
    data = H_z[H_z['Five-Digit ZIP Code'] == zip_]
    if data.shape[0] == 0:
        H_dic.append([zip_,None,None,None,None,None])
    else:
        P_i = data[data['Year']==2006]['HPI'].values[0]
        data['HPI_change'] = data['HPI'] - P_i
        P_n = data['HPI'].values[-1]
        min_ = min(data[(data['Year']>2005)&(data['Year']<2015)]['HPI_change'])
        H_dic.append([zip_,
                          P_i,
                          data[data['HPI_change']==min_]['Year'].values.tolist()[0],
                          min_,
                          data[data['Year']==2014]['HPI_change'].values.tolist()[0],
                      data[data['Year']==2018]['HPI_change'].values.tolist()[0],
                          P_n])

C:\Users\lingl\Anaconda3\lib\site-packages\ipykernel_launcher.py:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  # Remove the CWD from sys.path while we load stuff.


In [32]:
H_data = pd.DataFrame(H_dic,columns=['zip','2006','Year_low','low','2014','2018','Pay'])

In [33]:
H_data.head()

zip    2006  Year_low     low    2014   2018     Pay
0  85119.0  330.62      2011 -171.42 -108.91 -40.88  289.74
1  85120.0  357.82      2011 -216.30 -134.18 -17.86  339.96
2  85142.0  351.64      2011 -183.04 -100.38 -27.59  324.05
3  85201.0  438.00      2011 -257.07 -145.24 -16.12  421.88
4  85202.0  587.63      2011 -319.70 -169.88   5.62  593.25

In [34]:
z = 1+0.03

##### The score should both evaluate the opportunity cost, the investment income and fund cost ( the fund cost is calculated by using 3% as the annual rate)

In [35]:
H_data['score'] = (H_data['2014']*pow(1/z,2014 - 2006 +1) + H_data['low']*pow(1/z,2011 - 2006 +1) + pow(1/z,2018 - 2006 +1)*H_data['2018'])/H_data['2006']*H_data['Pay']-H_data['Pay']*pow(z,2018 - 2006 +1)

In [36]:
H_data['H_score'] = 1 + (max(H_data['score']) - H_data['score'])/min(H_data['score'])

In [37]:
H_data.head()

zip    2006  Year_low     low    2014   2018     Pay        score  \
0  85119.0  330.62      2011 -171.42 -108.91 -40.88  289.74  -648.848556   
1  85120.0  357.82      2011 -216.30 -134.18 -17.86  339.96  -780.608439   
2  85142.0  351.64      2011 -183.04 -100.38 -27.59  324.05  -705.353999   
3  85201.0  438.00      2011 -257.07 -145.24 -16.12  421.88  -944.704081   
4  85202.0  587.63      2011 -319.70 -169.88   5.62  593.25 -1269.092530   

    H_score  
0  0.801277  
1  0.697455  
2  0.756753  
3  0.568154  
4  0.312547

### E. Final recommondation

In [38]:
Zip_final = pd.merge(H_data[['zip','H_score']],result_s,on=['zip'])

In [39]:
Zip_final.head()

zip   H_score  similarity
0  85119.0  0.801277    0.340612
1  85120.0  0.697455    0.389743
2  85142.0  0.756753    0.197760
3  85201.0  0.568154    0.627745
4  85202.0  0.312547    0.616246

In [40]:
Zip_final['similarity'] = (Zip_final['similarity']-min(Zip_final['similarity']))/max(Zip_final['similarity'])## minmax scale 

In [41]:
Zip_final['Final_score']=Zip_final['H_score']+Zip_final['similarity'] 

In [42]:
Re = pd.merge(pd.merge(Zip_final.sort_values(by=['Final_score'], ascending=False).iloc[:5,:],L_d,on=['zip']),
              H_z[H_z['Year']==2018][['Five-Digit ZIP Code','HPI']],left_on=['zip'],right_on=['Five-Digit ZIP Code'])


### The final recommandation are the following place.

In [62]:
Re.drop(['Five-Digit ZIP Code','all_county_weights','military','timezone','parent_zcta','zcta','imprecise'],axis=1)

zip   H_score  similarity  Final_score       lat        lng      city  \
0  85233.0  0.859513    0.897551     1.757064  33.35209 -111.81136   Gilbert   
1  85298.0  1.000000    0.708440     1.708440  33.24188 -111.72573   Gilbert   
2  85234.0  0.878343    0.816493     1.694836  33.36454 -111.73944   Gilbert   
3  85249.0  0.940204    0.723349     1.663553  33.22551 -111.79707  Chandler   
4  85297.0  0.954878    0.700290     1.655168  33.27780 -111.73350   Gilbert   

  state_id state_name  population  density  county_fips county_name     HPI  
0       AZ    Arizona       37564   1490.5         4013    Maricopa  275.76  
1       AZ    Arizona       21479    579.5         4013    Maricopa  185.02  
2       AZ    Arizona       50014   1625.6         4013    Maricopa  261.09  
3       AZ    Arizona       36908   1031.7         4013    Maricopa  224.76  
4       AZ    Arizona       26979    987.0         4013    Maricopa  210.78